# Описание задачи


Многие знают про маркетплейсы где продаются б/у вещи, на которых есть возможность недорого купить качественную и полезную вещь. Но всегда волнует вопрос - кто и как устанавливает цену, и какие его характеристики больше всего влияют на итоговую стоимость продажи?! Вопрос становиться особо актуальным, если речь идет про дорогие товары, например про автомобили!    

В рамках данного исследования будет вестить работа с данными о продажах автомобилей на вторичном рынке. 

**Целью проекта будет *разработанная модель* предсказания стоимости автомобиля на вторичном рынке.**


## Данные
**train.csv** - информация о продажах (~440000) автомобилей с аукционов, которые будут использоваться в качестве обучающих данных.

**test.csv** - информация о продажах (~110000) автомобилей с аукционов, которые будут использоваться в качестве тестовых данных. Ваша задача - предсказать значение 'sellingprice' для каждого автомобиля из этого датасета.

**sample_submission.csv** - файл предсказаний в правильном формате.
vin - идентификатор каждого автомобиля в тестовом наборе.
sellingprice - Целевой признак. Для каждого автомобиля предскажите числовое значение стоимости автомобиля.

## Описание полей данных
`year` - год производства

`make` - производитель

`model` - модель

`trim` - модификация

`body` - тип кузова

`transmission` - тип КПП

`vin` - идентификатор (вин)

`state` - штат регистрации

`condition` - состояние по шкале (1-5)

`odometer` - пробег в милях

`color` - цвет кузова

`interior` - цвет интерьера

`seller` - продавец

`sellingprice` - стоимость продажи

`saledate` - дата продажи

## Ход решения задачи

Пошагово:

1. загрузка и ознакомление с данными,
2. предварительная обработка,
3. полноценный разведочный анализ,
4. разработка новых синтетических признаков,
5. проверка на мультиколлинеарность,
6. отбор финального набора обучающих признаков,
7. выбор и обучение моделей,
8. итоговая оценка качества предсказания лучшей модели,
9. анализ важности ее признаков.

### 1. Загрузка и ознакомление с данными

In [1]:
!pip install category_encoders -U

In [2]:
!pip install catboost -U

In [3]:
#импортируем необходимые для работы библиотеки
import pandas as pd
pd.set_option
pd.options.mode.chained_assignment = None
import matplotlib.pyplot as plt 
import numpy as np
import seaborn as sns

import catboost
from catboost import CatBoostRegressor
from catboost import Pool, cv



from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_validate

from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.linear_model import LinearRegression


from sklearn.preprocessing import OrdinalEncoder

#from sklearn.experimental import enable_iterative_imputer
#from sklearn.impute import SimpleImputer
#from sklearn.impute import IterativeImputer

from sklearn.base import TransformerMixin

#from sklearn.metrics import accuracy_score
#from sklearn.metrics import precision_score
#from sklearn.metrics import recall_score
#from sklearn.metrics import f1_score
#from sklearn.metrics import roc_auc_score
#from sklearn.metrics import recall_score
#from sklearn.metrics import mean_absolute_percentage_error 

После загрузки необходимых библиотек подгрузим датасеты

In [4]:
df_train = pd.read_csv('/Users/moygospodin/Documents/Practicum/Projects/Automobile_research/datasets/train.csv')
df_test = pd.read_csv('/Users/moygospodin/Documents/Practicum/Projects/Automobile_research/datasets/test.csv')

Проверим, что все отображается верно

In [5]:
display(df_train.head(5))
display(df_test.head(5))

year    make   model    trim   body transmission                vin state  \
0  2011    Ford    Edge     SEL    suv    automatic  2fmdk3jc4bba41556    md   
1  2014    Ford  Fusion      SE  Sedan    automatic  3fa6p0h75er208976    mo   
2  2012  Nissan  Sentra  2.0 SL  sedan    automatic  3n1ab6ap4cl698412    nj   
3  2003  HUMMER      H2    Base    suv    automatic  5grgn23u93h101360    tx   
4  2007    Ford  Fusion     SEL  Sedan    automatic  3fahp08z17r268380    md   

   condition  odometer  color interior                      seller  \
0        4.2  111041.0  black    black          santander consumer   
1        3.5   31034.0  black    black       ars/avis budget group   
2        2.2   35619.0  black    black          nissan-infiniti lt   
3        2.8  131301.0   gold    beige  wichita falls ford lin inc   
4        2.0  127709.0  black    black                purple heart   

   sellingprice                                 saledate  
0         12500  Tue Jun 02 2015 02:30:00 GMT-0700 (PDT)  
1         14500  Wed Feb 25 2015 02:00:00 GMT-0800 (PST)  
2          9100  Wed Jun 10 2015 02:30:00 GMT-0700 (PDT)  
3         13300  Wed Jun 17 2015 03:00:00 GMT-0700 (PDT)  
4          1300  Tue Feb 03 2015 04:00:00 GMT-0800 (PST)

year       make         model      trim      body transmission  \
0  2005   Cadillac           CTS      Base     Sedan    automatic   
1  2014        GMC  Savana Cargo      2500       Van          NaN   
2  2013     Nissan        Murano         S       SUV    automatic   
3  2013  Chevrolet        Impala  LS Fleet     Sedan    automatic   
4  2013     Nissan         Titan        SV  Crew Cab    automatic   

                 vin state  condition  odometer   color interior  \
0  1g6dp567450124779    ca        2.7  116970.0  silver    black   
1  1gtw7fca7e1902207    pa        4.4    6286.0   white     gray   
2  jn8az1mw6dw303497    oh        4.6   11831.0    gray    black   
3  2g1wf5e34d1160703    fl        2.3   57105.0  silver    black   
4  1n6aa0ec3dn301209    tn        2.9   31083.0   black    black   

                                             seller  \
0                            lexus of stevens creek   
1                                            u-haul   
2                                nissan-infiniti lt   
3  onemain rem/auto club of miami inc dba north dad   
4                         nissan north america inc.   

                                  saledate  
0  Wed Jan 14 2015 04:30:00 GMT-0800 (PST)  
1  Fri Feb 27 2015 01:00:00 GMT-0800 (PST)  
2  Tue Feb 24 2015 01:30:00 GMT-0800 (PST)  
3  Fri Mar 06 2015 02:00:00 GMT-0800 (PST)  
4  Wed Jun 03 2015 03:30:00 GMT-0700 (PDT)

### 2. Предобработка данных

Нужно посмотреть, все ли данные корректны в датасетах. Удалить дубликаты, если таковые имеются и убрать столбцы с данными, которые либо дублируют друг друга, либо не помогут в выполнении задачи. Проверить на выбросы и пропуски в данных.


In [6]:
#удалим столбцы
df_train = df_train.drop(['vin', 'seller', 'saledate'], axis=1)

In [7]:

df_test = df_test.drop(['vin', 'seller', 'saledate'], axis=1)

In [8]:
#for i in [df_train, df_test]:
#    display(i.info())
#    display(i.isna().sum())
#    display(i.duplicated().sum())

везде нижний регистр

In [9]:
df_train = df_train.applymap(lambda s: s.lower() if type(s) == str else s)
df_test = df_test.applymap(lambda s: s.lower() if type(s) == str else s)

In [10]:
#df_train['make'].unique()

In [11]:
def get_brands(df):
    df['make'] = df['make'].replace(['vw'], 'volkswagen')
    df['make'] = df['make'].replace(['gmc truck'], 'gmc')
    df['make'] = df['make'].replace(['mercedes-benz'], 'mercedes')
    df['make'] = df['make'].replace(['mazda tk'], 'mazda')
    df['make'] = df['make'].replace(['landrover'], 'land rover')
    df['make'] = df['make'].replace(['ford truck'], 'ford')
    df['make'] = df['make'].replace(['mercedes-b'], 'mercedes')
    df['make'] = df['make'].replace(['dodge tk'], 'dodge')
    

In [12]:
get_brands(df_train)
get_brands(df_test)

In [13]:
#df_train['body'].unique()

In [14]:
def get_body(df):
    df['body'] = df['body'].replace(['extended cab'], 'cab')
    df['body'] = df['body'].replace(['regular cab'], 'cab')
    df['body'] = df['body'].replace(['supercab'], 'cab')
    df['body'] = df['body'].replace(['g coupe'], 'goupe')
    df['body'] = df['body'].replace(['g convertible'], 'convertible')
    df['body'] = df['body'].replace(['access cab'], 'cab')
    df['body'] = df['body'].replace(['g sedan'], 'sedan')
    df['body'] = df['body'].replace(['e-series van'], 'van')
    df['body'] = df['body'].replace(['quad cab'], 'cab')
    df['body'] = df['body'].replace(['tsx sport wagon'], 'wagon')
    df['body'] = df['body'].replace(['cts coupe'], 'coupe')
    df['body'] = df['body'].replace(['koup'], 'coupe')
    df['body'] = df['body'].replace(['king cab'], 'cab')
    df['body'] = df['body'].replace(['double cab'], 'cab')
    df['body'] = df['body'].replace(['elantra coupe'], 'coupe')
    df['body'] = df['body'].replace(['genesis coupe'], 'coupe')
    df['body'] = df['body'].replace(['g37 coupe'], 'coupe')
    df['body'] = df['body'].replace(['club cab'], 'cab')
    df['body'] = df['body'].replace(['beetle convertible'], 'convertible')
    df['body'] = df['body'].replace(['mega cab'], 'cab')
    df['body'] = df['body'].replace(['regular-cab'], 'cab')
    df['body'] = df['body'].replace(['xtracab'], 'cab')
    df['body'] = df['body'].replace(['q60 coupe'], 'coupe')
    df['body'] = df['body'].replace(['promaster cargo van'], 'van')
    df['body'] = df['body'].replace(['cts-v coupe'], 'coupe')
    df['body'] = df['body'].replace(['cts wagon'], 'wagon')
    df['body'] = df['body'].replace(['cab plus 4'], 'cab')
    df['body'] = df['body'].replace(['g37 convertible'], 'convertible')
    df['body'] = df['body'].replace(['transit van'], 'van')
    df['body'] = df['body'].replace(['q60 convertible'], 'convertible')
    df['body'] = df['body'].replace(['cab plus'], 'cab')
    df['body'] = df['body'].replace(['ram van'], 'van')
    df['body'] = df['body'].replace(['granturismo convertible'], 'convertible')
    df['body'] = df['body'].replace(['cts-v wagon'], 'wagon')
    df['body'] = df['body'].replace(['crew cab'], 'cab')
    df['body'] = df['body'].replace(['supercrew'], 'cab')
    df['body'] = df['body'].replace(['crewmax cab'], 'cab')
    df['body'] = df['body'].replace(['goupe'], 'coupe')


In [15]:
get_body(df_train)
get_body(df_test)

In [16]:
#for i in df_train.columns:
#    display(df_train[i].value_counts())

In [17]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 440236 entries, 0 to 440235
Data columns (total 12 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          440236 non-null  int64  
 1   make          432193 non-null  object 
 2   model         432113 non-null  object 
 3   trim          431899 non-null  object 
 4   body          429843 non-null  object 
 5   transmission  388775 non-null  object 
 6   state         440236 non-null  object 
 7   condition     430831 non-null  float64
 8   odometer      440167 non-null  float64
 9   color         439650 non-null  object 
 10  interior      439650 non-null  object 
 11  sellingprice  440236 non-null  int64  
dtypes: float64(2), int64(2), object(8)
memory usage: 40.3+ MB



imp = IterativeImputer(max_iter=10, verbose=0)
imp.fit(df_train)
train_fill = imp.transform(df_train)
train_fill = pd.DataFrame(train_fill, columns=df_train.columns)

Заполняем пропуски

In [18]:
#df_train = df_train.fillna('unknown')
#df_test = df_test.fillna('unknown')


In [19]:
class DataFrameImputer(TransformerMixin):

    def __init__(self):
        """Impute missing values.

        Columns of dtype object are imputed with the most frequent value 
        in column.

        Columns of other types are imputed with mean of column.

        """
    def fit(self, X, y=None):

        self.fill = pd.Series([X[c].value_counts().index[0]
            if X[c].dtype == np.dtype('O') else X[c].mean() for c in X],
            index=X.columns)

        return self

    def transform(self, X, y=None):
        return X.fillna(self.fill)

In [20]:
df_train = DataFrameImputer().fit_transform(df_train)

In [22]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 440236 entries, 0 to 440235
Data columns (total 12 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          440236 non-null  int64  
 1   make          440236 non-null  object 
 2   model         440236 non-null  object 
 3   trim          440236 non-null  object 
 4   body          440236 non-null  object 
 5   transmission  440236 non-null  object 
 6   state         440236 non-null  object 
 7   condition     440236 non-null  float64
 8   odometer      440236 non-null  float64
 9   color         440236 non-null  object 
 10  interior      440236 non-null  object 
 11  sellingprice  440236 non-null  int64  
dtypes: float64(2), int64(2), object(8)
memory usage: 40.3+ MB


In [23]:
%%time
#тут работает энкодер
df_train = pd.DataFrame(OrdinalEncoder().fit_transform(df_train),
                            columns=df_train.columns)

CPU times: user 1.21 s, sys: 82.9 ms, total: 1.29 s
Wall time: 1.31 s


In [24]:
%%time
#тут работает энкодер
df_test = pd.DataFrame(OrdinalEncoder().fit_transform(df_test),
                            columns=df_test.columns)

CPU times: user 304 ms, sys: 18.9 ms, total: 323 ms
Wall time: 325 ms


In [25]:
features = df_train.drop(['sellingprice'], axis=1)
target = df_train['sellingprice']



In [26]:
features_test = df_test

In [27]:
#делим на выборки для обучения и валидации+тестирования
features_train, features_valid, target_train, target_valid = train_test_split(
    features, target, test_size=0.25, random_state=12345)

#features_train = df_train_fill.drop(['sellingprice'], axis=1)
#target_train = df_train_fill['sellingprice']

#features_test = df_test_fill


features_train = data.drop(['sellingprice'], axis=1)
target_train = data['sellingprice']

features_test = data_test


In [28]:
features_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 330177 entries, 187081 to 217570
Data columns (total 11 columns):
 #   Column        Non-Null Count   Dtype  
---  ------        --------------   -----  
 0   year          330177 non-null  float64
 1   make          330177 non-null  float64
 2   model         330177 non-null  float64
 3   trim          330177 non-null  float64
 4   body          330177 non-null  float64
 5   transmission  330177 non-null  float64
 6   state         330177 non-null  float64
 7   condition     330177 non-null  float64
 8   odometer      330177 non-null  float64
 9   color         330177 non-null  float64
 10  interior      330177 non-null  float64
dtypes: float64(11)
memory usage: 30.2 MB


In [29]:
cat = CatBoostRegressor(#loss_function = "RMSE",
                       #eval_metric = "MAPE",
                       random_state=1602)
#cat_features = [1,2,3,4,5,6,7,10,11,12,13]

In [30]:
%%time
params = {'depth': [4, 6, 10],
          'learning_rate' : [0.05, 0.1, 0.15],
          'l2_leaf_reg': [1,4,9],
          'iterations': [1000],
           'early_stopping_rounds':[800]
#           'loss_function':['MultiClass'],
          
         }

cb = cat
cb_b = GridSearchCV(cb, param_grid=params,
                      scoring='neg_mean_absolute_percentage_error', n_jobs=-1, cv=3)
cb_b.fit(features_train, target_train)


0:	learn: 284.2547345	total: 159ms	remaining: 2m 38s
1:	learn: 277.1512692	total: 195ms	remaining: 1m 37s
2:	learn: 270.5599853	total: 237ms	remaining: 1m 18s
3:	learn: 264.3423926	total: 275ms	remaining: 1m 8s
4:	learn: 258.5068792	total: 315ms	remaining: 1m 2s
5:	learn: 253.1485499	total: 356ms	remaining: 59s
6:	learn: 247.7070446	total: 397ms	remaining: 56.3s
7:	learn: 242.8244907	total: 473ms	remaining: 58.7s
8:	learn: 238.3984341	total: 513ms	remaining: 56.4s
9:	learn: 233.9782670	total: 555ms	remaining: 54.9s
10:	learn: 230.0522119	total: 597ms	remaining: 53.7s
11:	learn: 225.9300421	total: 629ms	remaining: 51.8s
12:	learn: 222.2224196	total: 669ms	remaining: 50.8s
13:	learn: 218.9256575	total: 701ms	remaining: 49.4s
14:	learn: 215.6338327	total: 737ms	remaining: 48.4s
15:	learn: 212.6059520	total: 778ms	remaining: 47.8s
16:	learn: 209.8303134	total: 812ms	remaining: 47s
17:	learn: 207.1559502	total: 852ms	remaining: 46.5s
18:	learn: 204.7245399	total: 895ms	remaining: 46.2s
19:	

0:	learn: 283.6993689	total: 145ms	remaining: 2m 25s
1:	learn: 276.8478226	total: 187ms	remaining: 1m 33s
2:	learn: 269.9215431	total: 224ms	remaining: 1m 14s
3:	learn: 263.7771714	total: 261ms	remaining: 1m 4s
4:	learn: 258.0155246	total: 294ms	remaining: 58.5s
5:	learn: 252.6192483	total: 325ms	remaining: 53.9s
6:	learn: 247.2205196	total: 358ms	remaining: 50.8s
7:	learn: 242.3899043	total: 391ms	remaining: 48.5s
8:	learn: 237.9842442	total: 426ms	remaining: 47s
9:	learn: 233.6622812	total: 516ms	remaining: 51.1s
10:	learn: 229.5642774	total: 550ms	remaining: 49.5s
11:	learn: 225.4564524	total: 602ms	remaining: 49.6s
12:	learn: 221.7971945	total: 636ms	remaining: 48.3s
13:	learn: 218.4327209	total: 680ms	remaining: 47.9s
14:	learn: 215.1046507	total: 717ms	remaining: 47.1s
15:	learn: 212.1508160	total: 749ms	remaining: 46s
16:	learn: 209.2690604	total: 789ms	remaining: 45.6s
17:	learn: 206.5153681	total: 828ms	remaining: 45.2s
18:	learn: 204.1215823	total: 873ms	remaining: 45.1s
19:	

0:	learn: 277.2671909	total: 154ms	remaining: 2m 34s
1:	learn: 264.5192310	total: 194ms	remaining: 1m 36s
2:	learn: 252.4623506	total: 234ms	remaining: 1m 17s
3:	learn: 242.5715774	total: 268ms	remaining: 1m 6s
4:	learn: 233.3199685	total: 310ms	remaining: 1m 1s
5:	learn: 225.4185667	total: 351ms	remaining: 58.1s
6:	learn: 218.6287780	total: 389ms	remaining: 55.1s
7:	learn: 212.1515630	total: 425ms	remaining: 52.6s
8:	learn: 206.6664028	total: 516ms	remaining: 56.8s
9:	learn: 201.5728050	total: 560ms	remaining: 55.4s
10:	learn: 197.2797298	total: 591ms	remaining: 53.2s
11:	learn: 193.5619514	total: 627ms	remaining: 51.6s
12:	learn: 190.0851302	total: 668ms	remaining: 50.7s
13:	learn: 187.0629320	total: 710ms	remaining: 50s
14:	learn: 184.4801080	total: 761ms	remaining: 50s
15:	learn: 182.2470092	total: 794ms	remaining: 48.9s
16:	learn: 180.2564619	total: 833ms	remaining: 48.1s
17:	learn: 178.1122126	total: 875ms	remaining: 47.7s
18:	learn: 176.1354311	total: 910ms	remaining: 47s
19:	le

306:	learn: 120.0563943	total: 11s	remaining: 24.9s
307:	learn: 119.9179477	total: 11.1s	remaining: 24.9s
308:	learn: 119.7945006	total: 11.1s	remaining: 24.9s
309:	learn: 119.6695358	total: 11.2s	remaining: 24.8s
310:	learn: 119.6096239	total: 11.2s	remaining: 24.8s
311:	learn: 119.4923867	total: 11.2s	remaining: 24.8s
312:	learn: 119.4582565	total: 11.3s	remaining: 24.7s
313:	learn: 119.4141550	total: 11.3s	remaining: 24.7s
314:	learn: 119.3033206	total: 11.3s	remaining: 24.6s
315:	learn: 119.2004638	total: 11.4s	remaining: 24.6s
316:	learn: 119.1190333	total: 11.4s	remaining: 24.6s
317:	learn: 119.0362189	total: 11.4s	remaining: 24.5s
318:	learn: 118.9535516	total: 11.5s	remaining: 24.5s
319:	learn: 118.8996142	total: 11.5s	remaining: 24.4s
320:	learn: 118.8043553	total: 11.5s	remaining: 24.4s
321:	learn: 118.7442179	total: 11.6s	remaining: 24.4s
322:	learn: 118.6645218	total: 11.6s	remaining: 24.3s
323:	learn: 118.6250097	total: 11.7s	remaining: 24.3s
324:	learn: 118.5358344	total:

306:	learn: 119.7575260	total: 11.1s	remaining: 25s
307:	learn: 119.6934083	total: 11.1s	remaining: 25s
308:	learn: 119.5315587	total: 11.1s	remaining: 24.9s
309:	learn: 119.3964429	total: 11.2s	remaining: 24.9s
310:	learn: 119.3330277	total: 11.2s	remaining: 24.8s
311:	learn: 119.2168167	total: 11.2s	remaining: 24.8s
312:	learn: 119.1504553	total: 11.3s	remaining: 24.8s
313:	learn: 119.0226210	total: 11.3s	remaining: 24.7s
314:	learn: 118.9489560	total: 11.3s	remaining: 24.7s
315:	learn: 118.8694242	total: 11.4s	remaining: 24.6s
316:	learn: 118.8258552	total: 11.4s	remaining: 24.6s
317:	learn: 118.7917231	total: 11.5s	remaining: 24.6s
318:	learn: 118.6862680	total: 11.5s	remaining: 24.5s
319:	learn: 118.5768957	total: 11.5s	remaining: 24.5s
320:	learn: 118.5094818	total: 11.6s	remaining: 24.5s
321:	learn: 118.4737575	total: 11.6s	remaining: 24.4s
322:	learn: 118.3484075	total: 11.6s	remaining: 24.4s
323:	learn: 118.3068033	total: 11.7s	remaining: 24.4s
324:	learn: 118.2772139	total: 1

...

476:	learn: 92.8547230	total: 11s	remaining: 12.1s
477:	learn: 92.7534579	total: 11s	remaining: 12s
478:	learn: 92.6994139	total: 11.1s	remaining: 12s
479:	learn: 92.6583009	total: 11.1s	remaining: 12s
480:	learn: 92.5685681	total: 11.1s	remaining: 12s
481:	learn: 92.5542585	total: 11.1s	remaining: 12s
482:	learn: 92.5108205	total: 11.1s	remaining: 11.9s
483:	learn: 92.4367422	total: 11.2s	remaining: 11.9s
484:	learn: 92.3937452	total: 11.2s	remaining: 11.9s
485:	learn: 92.3437125	total: 11.2s	remaining: 11.8s
486:	learn: 92.2924649	total: 11.2s	remaining: 11.8s
487:	learn: 92.2098925	total: 11.3s	remaining: 11.8s
488:	learn: 92.1720878	total: 11.3s	remaining: 11.8s
489:	learn: 92.1281783	total: 11.3s	remaining: 11.8s
490:	learn: 92.0812657	total: 11.3s	remaining: 11.7s
491:	learn: 92.0009699	total: 11.3s	remaining: 11.7s
492:	learn: 91.9688617	total: 11.4s	remaining: 11.7s
493:	learn: 91.8945249	total: 11.4s	remaining: 11.7s
494:	learn: 91.8411274	total: 11.4s	remaining: 11.6s
495:	le

636:	learn: 86.5786461	total: 14.6s	remaining: 8.34s
637:	learn: 86.5454541	total: 14.7s	remaining: 8.32s
638:	learn: 86.5176652	total: 14.7s	remaining: 8.3s
639:	learn: 86.5013683	total: 14.7s	remaining: 8.28s
640:	learn: 86.4810429	total: 14.7s	remaining: 8.25s
641:	learn: 86.4542412	total: 14.8s	remaining: 8.23s
642:	learn: 86.4182915	total: 14.8s	remaining: 8.2s
643:	learn: 86.3883398	total: 14.8s	remaining: 8.18s
644:	learn: 86.3374956	total: 14.8s	remaining: 8.15s
645:	learn: 86.3014177	total: 14.8s	remaining: 8.13s
646:	learn: 86.2600950	total: 14.9s	remaining: 8.11s
647:	learn: 86.2487948	total: 14.9s	remaining: 8.09s
648:	learn: 86.2264976	total: 14.9s	remaining: 8.06s
649:	learn: 86.2047782	total: 14.9s	remaining: 8.04s
650:	learn: 86.1867886	total: 14.9s	remaining: 8.01s
651:	learn: 86.1332429	total: 15s	remaining: 7.99s
652:	learn: 86.1227309	total: 15s	remaining: 7.96s
653:	learn: 86.0891826	total: 15s	remaining: 7.94s
654:	learn: 86.0251188	total: 15s	remaining: 7.92s
655

796:	learn: 82.0400330	total: 18.4s	remaining: 4.68s
797:	learn: 82.0105349	total: 18.4s	remaining: 4.66s
798:	learn: 82.0030726	total: 18.4s	remaining: 4.64s
799:	learn: 81.9760477	total: 18.5s	remaining: 4.62s
800:	learn: 81.9419655	total: 18.5s	remaining: 4.59s
801:	learn: 81.9173959	total: 18.5s	remaining: 4.57s
802:	learn: 81.8840118	total: 18.5s	remaining: 4.54s
803:	learn: 81.8350915	total: 18.5s	remaining: 4.52s
804:	learn: 81.8145484	total: 18.6s	remaining: 4.5s
805:	learn: 81.7929235	total: 18.6s	remaining: 4.48s
806:	learn: 81.7833298	total: 18.6s	remaining: 4.46s
807:	learn: 81.7687551	total: 18.7s	remaining: 4.44s
808:	learn: 81.7453828	total: 18.7s	remaining: 4.42s
809:	learn: 81.7287196	total: 18.7s	remaining: 4.39s
810:	learn: 81.6982555	total: 18.7s	remaining: 4.37s
811:	learn: 81.6786442	total: 18.8s	remaining: 4.34s
812:	learn: 81.6621333	total: 18.8s	remaining: 4.32s
813:	learn: 81.6515240	total: 18.8s	remaining: 4.3s
814:	learn: 81.6353398	total: 18.8s	remaining: 4

956:	learn: 78.7521996	total: 22s	remaining: 990ms
957:	learn: 78.7268501	total: 22.1s	remaining: 968ms
958:	learn: 78.7010224	total: 22.1s	remaining: 945ms
959:	learn: 78.6883398	total: 22.1s	remaining: 922ms
960:	learn: 78.6803471	total: 22.2s	remaining: 899ms
961:	learn: 78.6723851	total: 22.2s	remaining: 876ms
962:	learn: 78.6506769	total: 22.2s	remaining: 853ms
963:	learn: 78.6253550	total: 22.2s	remaining: 830ms
964:	learn: 78.6182617	total: 22.2s	remaining: 806ms
965:	learn: 78.5862726	total: 22.3s	remaining: 783ms
966:	learn: 78.5726546	total: 22.3s	remaining: 761ms
967:	learn: 78.5645854	total: 22.3s	remaining: 738ms
968:	learn: 78.5505584	total: 22.3s	remaining: 714ms
969:	learn: 78.5260480	total: 22.3s	remaining: 691ms
970:	learn: 78.4702104	total: 22.4s	remaining: 668ms
971:	learn: 78.4556539	total: 22.4s	remaining: 645ms
972:	learn: 78.4261498	total: 22.4s	remaining: 622ms
973:	learn: 78.4004357	total: 22.4s	remaining: 599ms
974:	learn: 78.3954569	total: 22.5s	remaining: 5

GridSearchCV(cv=3,
             estimator=<catboost.core.CatBoostRegressor object at 0x7fced46d9730>,
             n_jobs=-1,
             param_grid={'depth': [4, 6, 10], 'early_stopping_rounds': [800],
                         'iterations': [1000], 'l2_leaf_reg': [1, 4, 9],
                         'learning_rate': [0.05, 0.1, 0.15]},
             scoring='neg_mean_absolute_percentage_error')

In [31]:
cb_best = cb_b.best_estimator_


In [32]:
cb_best.get_params()

{'iterations': 1000,
 'learning_rate': 0.05,
 'depth': 6,
 'l2_leaf_reg': 9,
 'loss_function': 'RMSE',
 'random_state': 1602,
 'early_stopping_rounds': 800}

In [33]:
%%time
#это кросс-валидация

params = cb_best.get_params()
cv_dataset = Pool(data=features_valid,
                  label=target_valid)
scores = cv(cv_dataset,
            params,
            fold_count=2)

Training on fold [0/2]
0:	learn: 522.8773248	test: 523.2865842	best: 523.2865842 (0)	total: 8.79ms	remaining: 8.79s
1:	learn: 501.0941915	test: 501.5029556	best: 501.5029556 (1)	total: 13.5ms	remaining: 6.74s
2:	learn: 479.9962550	test: 480.4115629	best: 480.4115629 (2)	total: 18.2ms	remaining: 6.04s
3:	learn: 460.2007153	test: 460.5971343	best: 460.5971343 (3)	total: 22.8ms	remaining: 5.67s
4:	learn: 441.6886776	test: 442.0887330	best: 442.0887330 (4)	total: 27.5ms	remaining: 5.48s
5:	learn: 423.8439700	test: 424.2583697	best: 424.2583697 (5)	total: 32.3ms	remaining: 5.35s
6:	learn: 406.8416083	test: 407.1704638	best: 407.1704638 (6)	total: 36.9ms	remaining: 5.23s
7:	learn: 391.0322559	test: 391.3658399	best: 391.3658399 (7)	total: 41ms	remaining: 5.08s
8:	learn: 375.8087234	test: 376.1213959	best: 376.1213959 (8)	total: 45.4ms	remaining: 5s
9:	learn: 361.4685580	test: 361.7135502	best: 361.7135502 (9)	total: 49.9ms	remaining: 4.94s
10:	learn: 347.7991386	test: 347.9992311	best: 347.9

90:	learn: 139.6434646	test: 138.9726158	best: 138.9726158 (90)	total: 749ms	remaining: 7.48s
91:	learn: 139.1040928	test: 138.4505520	best: 138.4505520 (91)	total: 786ms	remaining: 7.75s
92:	learn: 138.6713821	test: 138.0454600	best: 138.0454600 (92)	total: 790ms	remaining: 7.71s
93:	learn: 138.3571616	test: 137.7477337	best: 137.7477337 (93)	total: 795ms	remaining: 7.66s
94:	learn: 138.1302527	test: 137.5184209	best: 137.5184209 (94)	total: 817ms	remaining: 7.79s
95:	learn: 137.7173427	test: 137.1212755	best: 137.1212755 (95)	total: 830ms	remaining: 7.81s
96:	learn: 137.5533552	test: 136.9575157	best: 136.9575157 (96)	total: 846ms	remaining: 7.88s
97:	learn: 137.3783953	test: 136.7801705	best: 136.7801705 (97)	total: 861ms	remaining: 7.93s
98:	learn: 136.8964733	test: 136.3098760	best: 136.3098760 (98)	total: 867ms	remaining: 7.89s
99:	learn: 136.6847223	test: 136.1173083	best: 136.1173083 (99)	total: 872ms	remaining: 7.85s
100:	learn: 136.5146356	test: 135.9466489	best: 135.9466489 

192:	learn: 117.7385469	test: 117.9320780	best: 117.9320780 (192)	total: 1.48s	remaining: 6.17s
193:	learn: 117.5609329	test: 117.7735658	best: 117.7735658 (193)	total: 1.48s	remaining: 6.17s
194:	learn: 117.3362577	test: 117.5544311	best: 117.5544311 (194)	total: 1.49s	remaining: 6.17s
195:	learn: 117.1105895	test: 117.3362867	best: 117.3362867 (195)	total: 1.5s	remaining: 6.17s
196:	learn: 117.0713556	test: 117.2968403	best: 117.2968403 (196)	total: 1.51s	remaining: 6.15s
197:	learn: 116.8530473	test: 117.0980200	best: 117.0980200 (197)	total: 1.51s	remaining: 6.13s
198:	learn: 116.6933636	test: 116.9397625	best: 116.9397625 (198)	total: 1.52s	remaining: 6.11s
199:	learn: 116.5521043	test: 116.8002519	best: 116.8002519 (199)	total: 1.52s	remaining: 6.1s
200:	learn: 116.3820920	test: 116.6271875	best: 116.6271875 (200)	total: 1.53s	remaining: 6.09s
201:	learn: 116.2305438	test: 116.4837108	best: 116.4837108 (201)	total: 1.54s	remaining: 6.07s
202:	learn: 116.0429281	test: 116.3057703	

293:	learn: 106.2640582	test: 106.8092948	best: 106.8092948 (293)	total: 2.07s	remaining: 4.98s
294:	learn: 106.1574059	test: 106.7051155	best: 106.7051155 (294)	total: 2.08s	remaining: 4.97s
295:	learn: 106.0608425	test: 106.5911772	best: 106.5911772 (295)	total: 2.09s	remaining: 4.97s
296:	learn: 105.9302557	test: 106.4624926	best: 106.4624926 (296)	total: 2.1s	remaining: 4.98s
297:	learn: 105.8318509	test: 106.3700081	best: 106.3700081 (297)	total: 2.11s	remaining: 4.98s
298:	learn: 105.8024528	test: 106.3413408	best: 106.3413408 (298)	total: 2.12s	remaining: 4.97s
299:	learn: 105.7179222	test: 106.2570818	best: 106.2570818 (299)	total: 2.13s	remaining: 4.96s
300:	learn: 105.5887854	test: 106.1305532	best: 106.1305532 (300)	total: 2.13s	remaining: 4.95s
301:	learn: 105.4934026	test: 106.0436643	best: 106.0436643 (301)	total: 2.13s	remaining: 4.93s
302:	learn: 105.4031563	test: 105.9379731	best: 105.9379731 (302)	total: 2.14s	remaining: 4.92s
303:	learn: 105.2999068	test: 105.8422340

388:	learn: 99.3405723	test: 100.1591810	best: 100.1591810 (388)	total: 2.67s	remaining: 4.19s
389:	learn: 99.2621504	test: 100.0825366	best: 100.0825366 (389)	total: 2.68s	remaining: 4.2s
390:	learn: 99.1969011	test: 100.0334054	best: 100.0334054 (390)	total: 2.69s	remaining: 4.2s
391:	learn: 99.1280511	test: 99.9676783	best: 99.9676783 (391)	total: 2.7s	remaining: 4.19s
392:	learn: 99.0466022	test: 99.8919300	best: 99.8919300 (392)	total: 2.71s	remaining: 4.18s
393:	learn: 99.0057167	test: 99.8538691	best: 99.8538691 (393)	total: 2.71s	remaining: 4.17s
394:	learn: 98.9483053	test: 99.7937678	best: 99.7937678 (394)	total: 2.71s	remaining: 4.16s
395:	learn: 98.8364705	test: 99.6884475	best: 99.6884475 (395)	total: 2.72s	remaining: 4.15s
396:	learn: 98.7613850	test: 99.6061523	best: 99.6061523 (396)	total: 2.73s	remaining: 4.14s
397:	learn: 98.7374390	test: 99.5894166	best: 99.5894166 (397)	total: 2.73s	remaining: 4.14s
398:	learn: 98.6507105	test: 99.5103688	best: 99.5103688 (398)	tota

...

623:	learn: 88.0263810	test: 90.4496110	best: 90.4496110 (623)	total: 4.19s	remaining: 2.52s
624:	learn: 87.9872921	test: 90.4069604	best: 90.4069604 (624)	total: 4.2s	remaining: 2.52s
625:	learn: 87.9735310	test: 90.3949490	best: 90.3949490 (625)	total: 4.21s	remaining: 2.51s
626:	learn: 87.9432870	test: 90.3684680	best: 90.3684680 (626)	total: 4.21s	remaining: 2.51s
627:	learn: 87.9071011	test: 90.3370095	best: 90.3370095 (627)	total: 4.22s	remaining: 2.5s
628:	learn: 87.8645629	test: 90.2959970	best: 90.2959970 (628)	total: 4.22s	remaining: 2.49s
629:	learn: 87.8364488	test: 90.2703966	best: 90.2703966 (629)	total: 4.23s	remaining: 2.48s
630:	learn: 87.7948610	test: 90.2270610	best: 90.2270610 (630)	total: 4.24s	remaining: 2.48s
631:	learn: 87.7681391	test: 90.2017606	best: 90.2017606 (631)	total: 4.24s	remaining: 2.47s
632:	learn: 87.7423344	test: 90.1781840	best: 90.1781840 (632)	total: 4.25s	remaining: 2.46s
633:	learn: 87.7280423	test: 90.1713417	best: 90.1713417 (633)	total: 4.

713:	learn: 85.2135197	test: 87.7865486	best: 87.7865486 (713)	total: 4.78s	remaining: 1.91s
714:	learn: 85.1898028	test: 87.7657889	best: 87.7657889 (714)	total: 4.79s	remaining: 1.91s
715:	learn: 85.1447225	test: 87.7219827	best: 87.7219827 (715)	total: 4.8s	remaining: 1.9s
716:	learn: 85.1143874	test: 87.6946387	best: 87.6946387 (716)	total: 4.81s	remaining: 1.9s
717:	learn: 85.0562746	test: 87.6415253	best: 87.6415253 (717)	total: 4.81s	remaining: 1.89s
718:	learn: 85.0386271	test: 87.6236324	best: 87.6236324 (718)	total: 4.82s	remaining: 1.88s
719:	learn: 85.0035740	test: 87.5936128	best: 87.5936128 (719)	total: 4.82s	remaining: 1.88s
720:	learn: 84.9883516	test: 87.5834015	best: 87.5834015 (720)	total: 4.83s	remaining: 1.87s
721:	learn: 84.9780737	test: 87.5770950	best: 87.5770950 (721)	total: 4.83s	remaining: 1.86s
722:	learn: 84.9453974	test: 87.5531659	best: 87.5531659 (722)	total: 4.83s	remaining: 1.85s
723:	learn: 84.9134125	test: 87.5243081	best: 87.5243081 (723)	total: 4.8

807:	learn: 82.6799596	test: 85.4189816	best: 85.4189816 (807)	total: 5.37s	remaining: 1.27s
808:	learn: 82.6654102	test: 85.4093341	best: 85.4093341 (808)	total: 5.38s	remaining: 1.27s
809:	learn: 82.6422381	test: 85.3875300	best: 85.3875300 (809)	total: 5.39s	remaining: 1.26s
810:	learn: 82.6073874	test: 85.3532317	best: 85.3532317 (810)	total: 5.41s	remaining: 1.26s
811:	learn: 82.5862310	test: 85.3366229	best: 85.3366229 (811)	total: 5.42s	remaining: 1.25s
812:	learn: 82.5569528	test: 85.3077532	best: 85.3077532 (812)	total: 5.42s	remaining: 1.25s
813:	learn: 82.4866830	test: 85.2237012	best: 85.2237012 (813)	total: 5.43s	remaining: 1.24s
814:	learn: 82.4579609	test: 85.1931462	best: 85.1931462 (814)	total: 5.43s	remaining: 1.23s
815:	learn: 82.4253320	test: 85.1639944	best: 85.1639944 (815)	total: 5.44s	remaining: 1.23s
816:	learn: 82.3896644	test: 85.1265042	best: 85.1265042 (816)	total: 5.44s	remaining: 1.22s
817:	learn: 82.3702882	test: 85.1084344	best: 85.1084344 (817)	total: 

907:	learn: 80.4292896	test: 83.2646133	best: 83.2646133 (907)	total: 5.97s	remaining: 605ms
908:	learn: 80.4102443	test: 83.2451181	best: 83.2451181 (908)	total: 5.99s	remaining: 599ms
909:	learn: 80.3920069	test: 83.2289303	best: 83.2289303 (909)	total: 6s	remaining: 594ms
910:	learn: 80.3691602	test: 83.2062975	best: 83.2062975 (910)	total: 6.01s	remaining: 587ms
911:	learn: 80.3513422	test: 83.1894759	best: 83.1894759 (911)	total: 6.01s	remaining: 580ms
912:	learn: 80.3324470	test: 83.1724676	best: 83.1724676 (912)	total: 6.02s	remaining: 574ms
913:	learn: 80.3064532	test: 83.1474161	best: 83.1474161 (913)	total: 6.02s	remaining: 567ms
914:	learn: 80.2923646	test: 83.1359483	best: 83.1359483 (914)	total: 6.03s	remaining: 560ms
915:	learn: 80.2750674	test: 83.1174487	best: 83.1174487 (915)	total: 6.03s	remaining: 553ms
916:	learn: 80.2450612	test: 83.0882702	best: 83.0882702 (916)	total: 6.04s	remaining: 546ms
917:	learn: 80.2256026	test: 83.0646957	best: 83.0646957 (917)	total: 6.0

CPU times: user 32.9 s, sys: 4.17 s, total: 37.1 s
Wall time: 13.9 s


In [34]:
predict_data = cb_best.predict(features_test)

In [35]:
predict_series = pd.Series(predict_data)

In [36]:
submission = pd.read_csv('/Users/moygospodin/Documents/Practicum/Projects/Automobile_research/datasets/test.csv')

In [37]:
submission = submission['vin']

In [38]:
submission = submission.to_frame()

In [39]:
submission['sellingprice'] = predict_series

In [40]:
submission.to_csv('sub6.csv', index=False)

In [41]:
submission.head()

vin  sellingprice
0  1g6dp567450124779    210.522486
1  1gtw7fca7e1902207    845.599238
2  jn8az1mw6dw303497    770.987784
3  2g1wf5e34d1160703    389.928702
4  1n6aa0ec3dn301209    748.490790

In [42]:
submission['sellingprice'].max()

1476.7847053639634

In [43]:
target_train.max()

1734.0

697:	learn: 57.8184728	total: 1m 26s	remaining: 37.4s
698:	learn: 57.7967457	total: 1m 26s	remaining: 37.3s
699:	learn: 57.7747081	total: 1m 26s	remaining: 37.2s
700:	learn: 57.7513382	total: 1m 26s	remaining: 37.1s
701:	learn: 57.7335943	total: 1m 26s	remaining: 36.9s
702:	learn: 57.7130276	total: 1m 27s	remaining: 36.8s
703:	learn: 57.7001635	total: 1m 27s	remaining: 36.7s
704:	learn: 57.6815120	total: 1m 27s	remaining: 36.5s
705:	learn: 57.6718255	total: 1m 27s	remaining: 36.4s
706:	learn: 57.6622651	total: 1m 27s	remaining: 36.3s
707:	learn: 57.6509850	total: 1m 27s	remaining: 36.2s
708:	learn: 57.6398322	total: 1m 27s	remaining: 36s
709:	learn: 57.6253209	total: 1m 27s	remaining: 35.9s
710:	learn: 57.6109420	total: 1m 28s	remaining: 35.8s
711:	learn: 57.5960356	total: 1m 28s	remaining: 35.7s
712:	learn: 57.5826592	total: 1m 28s	remaining: 35.5s
713:	learn: 57.5639151	total: 1m 28s	remaining: 35.4s
714:	learn: 57.5455875	total: 1m 28s	remaining: 35.3s
715:	learn: 57.5363605	total: 

687:	learn: 54.4742963	total: 1m 18s	remaining: 35.8s
688:	learn: 54.4527941	total: 1m 18s	remaining: 35.6s
689:	learn: 54.4363934	total: 1m 19s	remaining: 35.5s
690:	learn: 54.4164774	total: 1m 19s	remaining: 35.4s
691:	learn: 54.4016263	total: 1m 19s	remaining: 35.3s
692:	learn: 54.3870095	total: 1m 19s	remaining: 35.1s
693:	learn: 54.3673994	total: 1m 19s	remaining: 35s
694:	learn: 54.3540663	total: 1m 19s	remaining: 34.9s
695:	learn: 54.3352677	total: 1m 19s	remaining: 34.8s
696:	learn: 54.3204767	total: 1m 19s	remaining: 34.7s
697:	learn: 54.3069724	total: 1m 19s	remaining: 34.5s
698:	learn: 54.2974496	total: 1m 19s	remaining: 34.4s
699:	learn: 54.2847988	total: 1m 20s	remaining: 34.3s
700:	learn: 54.2691757	total: 1m 20s	remaining: 34.2s
701:	learn: 54.2472100	total: 1m 20s	remaining: 34.1s
702:	learn: 54.2387079	total: 1m 20s	remaining: 33.9s
703:	learn: 54.2218630	total: 1m 20s	remaining: 33.8s
704:	learn: 54.2080633	total: 1m 20s	remaining: 33.7s
705:	learn: 54.2018128	total: 

702:	learn: 54.3903925	total: 1m 17s	remaining: 32.6s
703:	learn: 54.3743635	total: 1m 17s	remaining: 32.5s
704:	learn: 54.3666376	total: 1m 17s	remaining: 32.4s
705:	learn: 54.3497681	total: 1m 17s	remaining: 32.3s
706:	learn: 54.3345624	total: 1m 17s	remaining: 32.2s
707:	learn: 54.3155950	total: 1m 17s	remaining: 32.1s
708:	learn: 54.3039238	total: 1m 17s	remaining: 31.9s
709:	learn: 54.2966923	total: 1m 17s	remaining: 31.8s
710:	learn: 54.2886415	total: 1m 18s	remaining: 31.7s
711:	learn: 54.2740424	total: 1m 18s	remaining: 31.6s
712:	learn: 54.2617301	total: 1m 18s	remaining: 31.5s
713:	learn: 54.2532887	total: 1m 18s	remaining: 31.4s
714:	learn: 54.2444021	total: 1m 18s	remaining: 31.2s
715:	learn: 54.2353000	total: 1m 18s	remaining: 31.1s
716:	learn: 54.2272300	total: 1m 18s	remaining: 31s
717:	learn: 54.2163491	total: 1m 18s	remaining: 30.9s
718:	learn: 54.2062658	total: 1m 18s	remaining: 30.8s
719:	learn: 54.1957803	total: 1m 18s	remaining: 30.7s
720:	learn: 54.1850458	total: 

604:	learn: 55.8195147	total: 54.5s	remaining: 35.6s
605:	learn: 55.7987744	total: 54.5s	remaining: 35.5s
606:	learn: 55.7726632	total: 54.6s	remaining: 35.4s
607:	learn: 55.7566262	total: 54.7s	remaining: 35.2s
608:	learn: 55.7411650	total: 54.7s	remaining: 35.1s
609:	learn: 55.7185489	total: 54.8s	remaining: 35s
610:	learn: 55.6988480	total: 54.8s	remaining: 34.9s
611:	learn: 55.6853428	total: 54.9s	remaining: 34.8s
612:	learn: 55.6742881	total: 55s	remaining: 34.7s
613:	learn: 55.6643055	total: 55s	remaining: 34.6s
614:	learn: 55.6428944	total: 55.1s	remaining: 34.5s
615:	learn: 55.6351238	total: 55.1s	remaining: 34.4s
616:	learn: 55.6176183	total: 55.2s	remaining: 34.3s
617:	learn: 55.6025667	total: 55.3s	remaining: 34.2s
618:	learn: 55.5884355	total: 55.3s	remaining: 34.1s
619:	learn: 55.5707122	total: 55.4s	remaining: 33.9s
620:	learn: 55.5514365	total: 55.5s	remaining: 33.8s
621:	learn: 55.5377865	total: 55.5s	remaining: 33.7s
622:	learn: 55.5247804	total: 55.6s	remaining: 33.6s